---
aliases:
- /2023/03/30/eprices
author: Jesse van Elteren
badges: true
branch: master
categories: [energy]
date: '2023-03-30'
description: How to profit
image: energy.jpg
output-file: 2023-03-30-eprices.html
title: Variation in electricity prices [In progress]
toc: false
---

This post is work in progress, nothing to see here at the moment :)

In [6]:
#| echo: false
import altair as alt
import pandas as pd
import numpy as np

rand = np.random.RandomState(42)

df = pd.DataFrame({
    'xval': range(100),
    'yval': rand.randn(100).cumsum()
})

slider = alt.binding_range(min=0, max=100, step=1)
cutoff = alt.param(bind=slider, value=50)

strategies = alt.binding_radio(options = ['', '2'])
test = alt.param(bind=strategies, value=50)


alt.Chart(df).mark_point().encode(
    x='xval',
    y='yval',
    color=alt.condition(
        alt.datum.xval < cutoff,
        alt.value('red'), alt.value('blue')
    )
).add_params(
    cutoff, test
    
)


alt.Chart(...)

In [12]:
import os
os.getcwd()

'd:\\Programmeren\\blog\\posts\\energy'

In [16]:
token = open('../../.tokens/ee', 'r').read()

FileNotFoundError: [Errno 2] No such file or directory: '../../.tokens/ee'

In [7]:
#| include: false
import pickle 
import math
import time
from collections import namedtuple
import pandas as pd
from entsoe import EntsoePandasClient
import altair as alt
alt.data_transformers.enable('default', max_rows=None)

%load_ext autoreload
%autoreload 2

token = open('../token', 'r').read()
client = EntsoePandasClient(api_key=token)

FileNotFoundError: [Errno 2] No such file or directory: '../token'

In [ ]:
#| include: false
# query transparency platform
start = pd.Timestamp('20170201', tz='Europe/Brussels')
end = pd.Timestamp('20230101', tz='Europe/Brussels')
country_code = 'NL'
prices = client.query_day_ahead_prices(country_code, start= start, end=end)
len(prices)

https://web-api.tp.entsoe.eu/api {'documentType': 'A44', 'in_Domain': '10YNL----------L', 'out_Domain': '10YNL----------L', 'securityToken': '09d5b83a-0730-40e4-a48b-62c6e22cb0a6', 'periodStart': '201701302300', 'periodEnd': '201802012300'}
https://web-api.tp.entsoe.eu/api {'documentType': 'A44', 'in_Domain': '10YNL----------L', 'out_Domain': '10YNL----------L', 'securityToken': '09d5b83a-0730-40e4-a48b-62c6e22cb0a6', 'periodStart': '201801302300', 'periodEnd': '201902012300'}
https://web-api.tp.entsoe.eu/api {'documentType': 'A44', 'in_Domain': '10YNL----------L', 'out_Domain': '10YNL----------L', 'securityToken': '09d5b83a-0730-40e4-a48b-62c6e22cb0a6', 'periodStart': '201901302300', 'periodEnd': '202002012300'}
https://web-api.tp.entsoe.eu/api {'documentType': 'A44', 'in_Domain': '10YNL----------L', 'out_Domain': '10YNL----------L', 'securityToken': '09d5b83a-0730-40e4-a48b-62c6e22cb0a6', 'periodStart': '202001302300', 'periodEnd': '202102012300'}
https://web-api.tp.entsoe.eu/api {'d

51841

In [ ]:
#| include: false
# change the series into a dataframe
df = pd.DataFrame(prices, columns=['price'])

# create datetime, hour, and date columns
df['datetime'] = pd.to_datetime(df.index)
df['hour'] = df['datetime'].dt.hour
df['date'] = df['datetime'].dt.date

# calculate hourly mean prices and reshape into a daily DataFrame
df = df.groupby(['date', 'hour']).mean(numeric_only=True).unstack('hour')

# compute minimum and maximum daily price
df['min'] = df.min(axis=1)
df['max'] = df.max(axis=1)
df['mean'] = df.mean(axis=1)
df['stdev'] = df.std(axis=1)

# compute price spread
df['spread'] = df['max'] - df['min']
df.drop(df.index[-1], inplace=True)
df.index = pd.to_datetime(df.index)

# add time elements
df['year'] = df.index.year
df['month'] = df.index.month
df['weekday'] = df.index.day_name()
df['weekday'] = df['weekday'].apply(lambda x: x[:3])
df['date'] = df.index
df.head()


price                                                          \
hour            0      1      2      3      4      5      6      7      8   
date                                                                        
2017-02-01  39.62  36.40  35.80  36.40  36.40  37.00  42.40  60.41  72.85   
2017-02-02  31.17  30.14  32.86  32.30  31.05  32.66  39.91  55.58  57.19   
2017-02-03  39.50  34.92  34.26  32.55  32.49  35.85  43.02  56.32  60.00   
2017-02-04  37.04  34.96  34.01  31.93  31.89  32.09  33.82  37.04  42.32   
2017-02-05  70.16  57.24  37.73  36.65  33.15  34.55  31.92  36.93  43.41   

                   ...           min    max       mean      stdev spread  \
hour            9  ...     23                                              
date               ...                                                     
2017-02-01  65.89  ...  38.10  35.80  72.85  50.175769  11.920769  37.05   
2017-02-02  59.10  ...  36.77  30.14  59.10  45.133077  10.493333  28.96   
2017-02-03  58.00  ...  36.08  32.49  60.00  47.370769   9.476727  27.51   
2017-02-04  49.58  ...  45.70  31.89  66.18  45.688077  10.294485  34.29   
2017-02-05  50.34  ...  50.19  31.92  70.16  49.259231  12.016233  38.24   

            year month weekday       date  
hour                                       
date                                       
2017-02-01  2017     2     Wed 2017-02-01  
2017-02-02  2017     2     Thu 2017-02-02  
2017-02-03  2017     2     Fri 2017-02-03  
2017-02-04  2017     2     Sat 2017-02-04  
2017-02-05  2017     2     Sun 2017-02-05  

[5 rows x 33 columns]

In [ ]:
#| include: false
import math
minn  = math.floor(min(prices)/100)*100
maxx = math.ceil(max(prices)/100)*100
minn, maxx

(-300, 900)

In [ ]:
#| include: false
# also compute normalized prices done as a min max scaler
normalized_prices = (df['price'] -  df['min'].values[:,None]) / df['spread'].values[:,None]
multi_index = pd.MultiIndex.from_product([['normalized'], normalized_prices.columns])

# assign the MultiIndex to the DataFrame columns
normalized_prices.columns = multi_index
df = pd.concat([df, normalized_prices], axis=1)

### Slice prices

In [ ]:
#| include: false
total = pd.DataFrame(prices).reset_index()
total.columns = ['datetime', 'price']

hourly = alt.Chart(total, title="Hourly electricity price").mark_line().encode(
    x = alt.X('datetime', title=None),
    y=alt.Y('price', axis=alt.Axis(title='Price [cents/kw]'), scale=alt.Scale(domain=(minn, maxx))),
    strokeWidth=alt.value(0.07)
)

In [ ]:
#| echo: false
total = df[['spread']].reset_index().melt('date')
total.columns = ['date', 'type', '', 'price']

domain = ['spread']
range_ = ['red']
spread = alt.Chart(total, title="Daily spread between min/max").mark_line().encode(
    x = alt.X('date', title=None),
    y=alt.Y('price', axis=alt.Axis(title='Price spread [cents/kw]'), scale=alt.Scale(domain=(minn, maxx))),
    color = alt.Color('type', scale=alt.Scale(domain=domain, range=range_)),
    strokeWidth=alt.value(0.25)
)
hourly | spread

d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.HConcatChart(...)

From 2021 onwards things have been 'interesting'! There are huge swings in the prices, both between the days, but also within the days. The right graph shows that daily changes are also large

In [ ]:
#| include: false
yearmonth = df.groupby(['year', 'month']).mean()['mean'].reset_index()

line = alt.Chart(yearmonth).mark_line().encode(
    x = 'month:N',
    y='mean',
    color='year:O',
    tooltip='year'
)

labels = alt.Chart(yearmonth).mark_text(align='left', dx=3).encode(
    alt.X('month:N', aggregate='max'),
    alt.Y('mean:Q', aggregate={'argmax': 'month'}, scale=alt.Scale(type='linear')),
    alt.Text('year'),
    alt.Color('year:N', legend=None),#scale=alt.Scale(domain=countries_list,type='ordinal')), 
)

line + labels

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2407848160.py:2: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  yearmonth = df.groupby(['year', 'month']).mean()['mean'].reset_index()
C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2407848160.py:2: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  yearmonth = df.groupby(['year', 'month']).mean()['mean'].reset_index()
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.LayerChart(...)

Monthly does not show a lot

In [ ]:
#| include: false
yearweekday = df.groupby(['year', 'weekday']).mean()['mean'].reset_index()
weekdays = ["Mon", 'Tue', "Wed", 'Thu', 'Fri', 'Sat', 'Sun']
line = alt.Chart(yearweekday).mark_line().encode(
    x = alt.X('weekday:N', title='Dag van de week'),
    y=alt.Y('mean', title='test'),
    color='year:O',
    tooltip='year'
)

labels = alt.Chart(yearweekday).mark_text(align='left', dx=3).encode(
    alt.X('weekday:N', aggregate='max'),
    alt.Y('mean:Q', aggregate={'argmax': 'weekday'}, scale=alt.Scale(type='linear')),
    alt.Text('year'),
    alt.Color('year:N', legend=None),#scale=alt.Scale(domain=countries_list,type='ordinal')), 
)

line + labels

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2464960495.py:2: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  yearweekday = df.groupby(['year', 'weekday']).mean()['mean'].reset_index()
C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2464960495.py:2: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  yearweekday = df.groupby(['year', 'weekday']).mean()['mean'].reset_index()
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.LayerChart(...)

In the weekend (day 5 and 6), prices are somewhat lower compared to the weekdays. Mind the sorting this is not OK yet

In [ ]:
#| echo: false
test = df.groupby('year').mean()['price'].reset_index()
test = test.melt('year')
test.head()

line= alt.Chart(test, title='Hourly average prices by year').mark_line().encode(
    x = alt.X('hour:N', title='Hour of the day'),
    y=alt.Y('value',title='Average price [cents/kw]'),
    color='year:O',
    tooltip='year'
)

labels = alt.Chart(test).mark_text(align='left', dx=3).encode(
    alt.X('hour:N', aggregate='max'),
    alt.Y('value:Q', aggregate={'argmax': 'hour'}, scale=alt.Scale(type='linear')),
    alt.Text('year'),
    alt.Color('year:N', legend=None),#scale=alt.Scale(domain=countries_list,type='ordinal')), 
)

line + labels

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\827378211.py:2: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  test = df.groupby('year').mean()['price'].reset_index()
C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\827378211.py:2: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  test = df.groupby('year').mean()['price'].reset_index()
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.LayerChart(...)

These are the mean hourly prices. Prices are highest at 8:00 and 19:00, and lowest at 3:00 and 13:00. The lowest prices used to be in the night, but that has changed to 13:00.

### Spreads

In [ ]:
#| include: false
# spread over time
spread = df.reset_index(drop=True).groupby('date').mean()['spread'].reset_index()
alt.Chart(spread).mark_line().encode(
    x = 'date',
    y='spread',
    strokeWidth=alt.value(0.4)
)

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\1318744073.py:3: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  spread = df.reset_index(drop=True).groupby('date').mean()['spread'].reset_index()
C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\1318744073.py:3: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  spread = df.reset_index(drop=True).groupby('date').mean()['spread'].reset_index()
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

In [ ]:
#| include: false
# std over time, almost same result
spread = df.reset_index(drop=True).groupby('date').mean()['stdev'].reset_index()
alt.Chart(spread).mark_line().encode(
    x = 'date',
    y='stdev',
    strokeWidth=alt.value(0.4)
)

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\520559747.py:3: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  spread = df.reset_index(drop=True).groupby('date').mean()['stdev'].reset_index()
C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\520559747.py:3: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  spread = df.reset_index(drop=True).groupby('date').mean()['stdev'].reset_index()
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

### Normalized prices

In [ ]:
#| include: false
test = df[df['year']==2022].reset_index(drop=True).groupby('date').mean()['normalized'].reset_index()
test = test.melt('date')

stripplot =  alt.Chart(test, width=40).mark_circle(size=8).encode(
    x=alt.X(
        'jitter:Q',
        title=None,
        axis=alt.Axis(values=[0], ticks=True, grid=False, labels=False),
        scale=alt.Scale(),
    ),
    y=alt.Y('value:Q'),
    color=alt.Color('hour:N', legend=None),
    column=alt.Column(
        'hour:N',
        header=alt.Header(
            labelAngle=-90,
            titleOrient='top',
            labelOrient='bottom',
            labelAlign='right',
            labelPadding=3,
        ),
    ),
).transform_calculate(
    # Generate Gaussian jitter with a Box-Muller transform
    jitter='sqrt(-2*log(random()))*cos(2*PI*random())'
).configure_facet(
    spacing=0
).configure_view(
    stroke=None
)
stripplot

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2088698996.py:1: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  test = df[df['year']==2022].reset_index(drop=True).groupby('date').mean()['normalized'].reset_index()
C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2088698996.py:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  test = df[df['year']==2022].reset_index(drop=True).groupby('date').mean()['normalized'].reset_index()
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

In [ ]:
#| echo: false
test = (df.groupby('year').mean())['normalized'].reset_index()
test = test.melt('year')
test.head()

line= alt.Chart(test).mark_line().encode(
    x = 'hour:N',
    y='value',
    color='year:O',
    tooltip='year'
)

labels = alt.Chart(test).mark_text(align='left', dx=3).encode(
    alt.X('hour:N', aggregate='max'),
    alt.Y('value:Q', aggregate={'argmax': 'hour'}, scale=alt.Scale(type='linear')),
    alt.Text('year'),
    alt.Color('year:N', legend=None),#scale=alt.Scale(domain=countries_list,type='ordinal')), 
)

line + labels

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2070120334.py:1: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  test = (df.groupby('year').mean())['normalized'].reset_index()
C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2070120334.py:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  test = (df.groupby('year').mean())['normalized'].reset_index()
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.LayerChart(...)

### How much is this variation worth for you?

In [ ]:
#| include: false
# calculate strategies
kw = 2.5
df['bestgain'] = df['spread'] * kw
df['realgain'] = (df['mean'] - df['min']) * kw
df['dinnershift'] = (df[('price',19)] - df[('price',13)]) * kw
df['morningshift'] = (df[('price',9)] - df[('price',13)]) * kw

outcomes = df[df['year']==2022].groupby('year')[[('bestgain', ''), ('realgain', ''), ('dinnershift',''), ('morningshift','')]].sum() // 100
outcomes.sum()

              hour
bestgain              1871.0
realgain               900.0
dinnershift           1236.0
morningshift           760.0
dtype: float64

In [ ]:
#| include: false
t = df.groupby(('year','')).mean()['price'].reset_index()
t.melt()

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\2685143580.py:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  t = df.groupby(('year','')).mean()['price'].reset_index()


hour        value
0    (year, )  2017.000000
1    (year, )  2018.000000
2    (year, )  2019.000000
3    (year, )  2020.000000
4    (year, )  2021.000000
..        ...          ...
145        23    49.835370
146        23    38.100247
147        23    30.440574
148        23    96.095288
149        23   240.013699

[150 rows x 2 columns]

In [ ]:
#| include: false
out = df.copy()
out.columns = out.columns.get_level_values(0)
out = out.loc[:,~out.columns.duplicated()].copy()
out.columns

Index(['price', 'min', 'max', 'mean', 'stdev', 'spread', 'year', 'month',
       'weekday', 'date', 'normalized', 'bestgain', 'realgain', 'dinnershift',
       'morningshift'],
      dtype='object')

In [ ]:
#| include: false
out.groupby('weekday').mean().reset_index()

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\3100116716.py:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  out.groupby('weekday').mean().reset_index()


weekday      price        min         max       mean      stdev     spread  \
0     Fri  80.812621  59.091489  122.289871  89.061553  19.936583  63.198382   
1     Mon  75.704773  56.499481  128.756981  89.120984  22.682931  72.257500   
2     Sat  83.784628  45.163495  110.341618  76.808575  19.866522  65.178123   
3     Sun  77.065032  34.696201  110.407662  70.021372  23.030862  75.711461   
4     Thu  80.184498  60.703139  128.137249  91.443688  20.992150  67.434110   
5     Tue  78.506429  61.244708  131.802240  92.327707  22.228411  70.557532   
6     Wed  79.621909  60.277184  129.405146  91.277353  21.364682  69.127961   

          year     month  normalized    bestgain   realgain  dinnershift  \
0  2019.537217  6.608414    0.277535  157.995955  74.925162    72.116828   
1  2019.535714  6.607143    0.261739  180.643750  81.553759    82.312013   
2  2019.540453  6.601942    0.497314  162.945307  79.112699   102.754045   
3  2019.532468  6.613636    0.491633  189.278653  88.312927   123.282224   
4  2019.533981  6.611650    0.241397  168.585275  76.851372    84.101537   
5  2019.538961  6.600649    0.216896  176.393831  77.707499    87.132549   
6  2019.533981  6.579288    0.226786  172.819903  77.500420    83.222168   

   morningshift  
0     70.984951  
1     55.587662  
2     65.161003  
3     41.704221  
4     64.227589  
5     61.913880  
6     59.482282

In [ ]:
#| echo: false
alt.Chart(out.groupby('weekday').mean().reset_index()).mark_circle(size=60).encode(
    x='weekday',
    y='bestgain',
)

C:\Users\Gebruiker\AppData\Local\Temp\ipykernel_16052\274796445.py:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  alt.Chart(out.groupby('weekday').mean().reset_index()).mark_circle(size=60).encode(
d:\Programmeren\adventofcode\.aocenvpy311\Lib\site-packages\altair\utils\core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

In [ ]:
#| include: false
df_perc = df_perc.melt(id_vars=['date'])
df_perc['date'] = df_perc['date'].astype(str)
df_perc.head()

date hour  value
0  2017-02-01    0  39.62
1  2017-02-02    0  31.17
2  2017-02-03    0  39.50
3  2017-02-04    0  37.04
4  2017-02-05    0  70.16